In [1]:
import pandas as pd
import torch
from torch.autograd import Variable
import torch.nn.functional as F
from torch import nn
from torch.utils.data import DataLoader, TensorDataset
from imblearn.over_sampling import SMOTE
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import f1_score
from sklearn.metrics import confusion_matrix

In [2]:
# read csv
# https://research.unsw.edu.au/projects/unsw-nb15-dataset
# According to the website above csv is wrongly saved, so I change the name
# The number of records in the training set is 175,341 records and the testing set is 82,332 records from the different types, attack and normal.
df = pd.read_csv('../Data/UNSW_NB15_testing-set.csv')

In [3]:
# nominal to numeric of data
# proto                 object
# service               object
# state                 object

# proto to numeric
# proto_mapping = {'xxx':2, 'xxx':1, 'xxx':0}
# data['proto'] = data['proto'].map(proto_mapping)

# proto to numeric
proto_le = LabelEncoder()
df['proto'] = proto_le.fit_transform(df['proto'])
 
# service to numeric
service_le = LabelEncoder()
df['service'] = service_le.fit_transform(df['service'])

# state to numeric
state_le = LabelEncoder()
df['state'] = state_le.fit_transform(df['state'])

# nominal to numeric of data
# attack_cat            object

# target to numeric
attack_cat_le = LabelEncoder()
df['attack_cat'] = attack_cat_le.fit_transform(df['attack_cat'])

df.head(10)

id       dur  proto  service  state  spkts  dpkts  sbytes  dbytes  \
0   1  0.121478    113        0      2      6      4     258     172   
1   2  0.649902    113        0      2     14     38     734   42014   
2   3  1.623129    113        0      2      8     16     364   13186   
3   4  1.681642    113        3      2     12     12     628     770   
4   5  0.449454    113        0      2     10      6     534     268   
5   6  0.380537    113        0      2     10      6     534     268   
6   7  0.637109    113        0      2     10      8     534     354   
7   8  0.521584    113        0      2     10      8     534     354   
8   9  0.542905    113        0      2     10      8     534     354   
9  10  0.258687    113        0      2     10      6     534     268   

        rate  ...  ct_dst_sport_ltm  ct_dst_src_ltm  is_ftp_login  ct_ftp_cmd  \
0  74.087490  ...                 1               1             0           0   
1  78.473372  ...                 1               2             0           0   
2  14.170161  ...                 1               3             0           0   
3  13.677108  ...                 1               3             1           1   
4  33.373826  ...                 1              40             0           0   
5  39.417980  ...                 1              40             0           0   
6  26.683033  ...                 1              40             0           0   
7  32.593026  ...                 1              40             0           0   
8  31.313031  ...                 1              40             0           0   
9  57.985135  ...                 1              40             0           0   

   ct_flw_http_mthd  ct_src_ltm  ct_srv_dst  is_sm_ips_ports  attack_cat  \
0                 0           1           1                0           6   
1                 0           1           6                0           6   
2                 0           2           6                0           6   
3                 0           2           1                0           6   
4                 0           2          39                0           6   
5                 0           2          39                0           6   
6                 0           1          39                0           6   
7                 0           3          39                0           6   
8                 0           3          39                0           6   
9                 0           3          39                0           6   

   label  
0      0  
1      0  
2      0  
3      0  
4      0  
5      0  
6      0  
7      0  
8      0  
9      0  

[10 rows x 45 columns]

In [4]:
df_train, df_test = train_test_split(df, test_size=0.3, random_state=0)

In [5]:
#df_train.dtypes
df_train.shape

(122738, 45)

In [6]:
data_train = df_train.drop(['id', 'label', 'attack_cat'], axis=1)
label_train = df_train.iloc[:,-1]
data_train.head(10)

dur  proto  service  state  spkts  dpkts  sbytes  dbytes  \
41479   0.581798    113        0      2     10      6     588     268   
174119  0.000009    119        2      3      2      0     114       0   
39585   0.294033    113        4      2      8     12     424    8824   
23269   0.001059    119        2      0      2      2     146     178   
35227   1.433471    113        3      2     52     54    2934    3742   
157804  0.000003    119        2      3      2      0     114       0   
170646  1.434152    113        4      2     10      8     450     782   
102714  1.725872    113        5      2     10     10     798    1730   
138365  0.000001    119        2      3      2      0     114       0   
7840    0.528823    113        9      2     52     42   37372    3380   

                rate  sttl  ...  ct_dst_ltm  ct_src_dport_ltm  \
41479   2.578214e+01   254  ...           2                 1   
174119  1.111111e+05   254  ...          15                15   
39585   6.461860e+01    31  ...          11                 1   
23269   2.832861e+03    31  ...           2                 1   
35227   7.324878e+01    31  ...           4                 1   
157804  3.333333e+05   254  ...          12                12   
170646  1.185370e+01    62  ...           2                 1   
102714  1.100893e+01    62  ...           1                 1   
138365  1.000000e+06   254  ...          16                16   
7840    1.758622e+02    31  ...           2                 1   

        ct_dst_sport_ltm  ct_dst_src_ltm  is_ftp_login  ct_ftp_cmd  \
41479                  1               1             0           0   
174119                15              31             0           0   
39585                  1               5             0           0   
23269                  1               1             0           0   
35227                  1               5             1           1   
157804                12              14             0           0   
170646                 1               2             0           0   
102714                 1               1             0           0   
138365                16              18             0           0   
7840                   1               3             0           0   

        ct_flw_http_mthd  ct_src_ltm  ct_srv_dst  is_sm_ips_ports  
41479                  0           1           5                0  
174119                 0          15          31                0  
39585                  0           3           6                0  
23269                  0           4           2                0  
35227                  0           6           2                0  
157804                 0          12          14                0  
170646                 0           4           1                0  
102714                 1           1           1                0  
138365                 0          16          18                0  
7840                   0           4           1                0  

[10 rows x 42 columns]

In [7]:
#min-max scaling
data_train_norm = (data_train - data_train.min()) / (data_train.max() - data_train.min())
data_train_norm = data_train_norm.fillna(0)

In [8]:
data_train_norm.shape
data_train_norm.head(10)

dur     proto   service     state     spkts     dpkts  \
41479   9.696635e-03  0.856061  0.000000  0.285714  0.000936  0.000553   
174119  1.500000e-07  0.901515  0.166667  0.428571  0.000104  0.000000   
39585   4.900551e-03  0.856061  0.333333  0.285714  0.000728  0.001106   
23269   1.765000e-05  0.901515  0.166667  0.000000  0.000104  0.000184   
35227   2.389119e-02  0.856061  0.250000  0.285714  0.005304  0.004977   
157804  5.000001e-08  0.901515  0.166667  0.428571  0.000104  0.000000   
170646  2.390254e-02  0.856061  0.333333  0.285714  0.000936  0.000737   
102714  2.876454e-02  0.856061  0.416667  0.285714  0.000936  0.000922   
138365  1.666667e-08  0.901515  0.166667  0.428571  0.000104  0.000000   
7840    8.813718e-03  0.856061  0.750000  0.285714  0.005304  0.003871   

          sbytes    dbytes      rate      sttl  ...  ct_dst_ltm  \
41479   0.000042  0.000018  0.000026  0.996078  ...        0.02   
174119  0.000005  0.000000  0.111111  0.996078  ...        0.28   
39585   0.000029  0.000609  0.000065  0.121569  ...        0.20   
23269   0.000008  0.000012  0.002833  0.121569  ...        0.02   
35227   0.000223  0.000258  0.000073  0.121569  ...        0.06   
157804  0.000005  0.000000  0.333333  0.996078  ...        0.22   
170646  0.000031  0.000054  0.000012  0.243137  ...        0.02   
102714  0.000058  0.000119  0.000011  0.243137  ...        0.00   
138365  0.000005  0.000000  1.000000  0.996078  ...        0.30   
7840    0.002879  0.000233  0.000176  0.121569  ...        0.02   

        ct_src_dport_ltm  ct_dst_sport_ltm  ct_dst_src_ltm  is_ftp_login  \
41479               0.00          0.000000        0.000000          0.00   
174119              0.28          0.311111        0.483871          0.00   
39585               0.00          0.000000        0.064516          0.00   
23269               0.00          0.000000        0.000000          0.00   
35227               0.00          0.000000        0.064516          0.25   
157804              0.22          0.244444        0.209677          0.00   
170646              0.00          0.000000        0.016129          0.00   
102714              0.00          0.000000        0.000000          0.00   
138365              0.30          0.333333        0.274194          0.00   
7840                0.00          0.000000        0.032258          0.00   

        ct_ftp_cmd  ct_flw_http_mthd  ct_src_ltm  ct_srv_dst  is_sm_ips_ports  
41479         0.00          0.000000    0.000000    0.065574              0.0  
174119        0.00          0.000000    0.237288    0.491803              0.0  
39585         0.00          0.000000    0.033898    0.081967              0.0  
23269         0.00          0.000000    0.050847    0.016393              0.0  
35227         0.25          0.000000    0.084746    0.016393              0.0  
157804        0.00          0.000000    0.186441    0.213115              0.0  
170646        0.00          0.000000    0.050847    0.000000              0.0  
102714        0.00          0.033333    0.000000    0.000000              0.0  
138365        0.00          0.000000    0.254237    0.278689              0.0  
7840          0.00          0.000000    0.050847    0.000000              0.0  

[10 rows x 42 columns]

In [9]:
train_X = torch.tensor(data_train_norm.values, dtype=torch.float32)
train_Y = torch.tensor(label_train.values, dtype=torch.long) 
train = TensorDataset(train_X, train_Y)

In [10]:
train_loader = DataLoader(train, batch_size=100, shuffle=True)
# drop_last = True

In [11]:
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.fc1 = nn.Linear(42, 850)
        self.fc2 = nn.Linear(850, 2)
        
    def forward(self, x):
        x = F.relu(self.fc1(x)) # ReLU: max(x, 0)
        x = self.fc2(x)
        # return F.log_softmax(x, dim=1)
        return x

model = Net()

In [12]:
print(torch.cuda.is_available())

True


In [13]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = model.to(device)
print(device)

cuda


In [14]:
criterion = nn.CrossEntropyLoss()

In [15]:
#optimizer = torch.optim.SGD(model.parameters(), lr=0.03)
optimizer = torch.optim.Adam(model.parameters(), lr=0.03)

In [16]:
model.train()

Net(
  (fc1): Linear(in_features=42, out_features=850, bias=True)
  (fc2): Linear(in_features=850, out_features=2, bias=True)
)

In [17]:
#Training the machine learning model
loss_list=[]
for epoch in range(100): #learning 100 times
    #total_loss = 0
    model.train()
    for train_x, train_y in train_loader:
        train_x, train_y = Variable(train_x), Variable(train_y)
        train_x = train_x.to(device)
        train_y = train_y.to(device)
        optimizer.zero_grad()
        output = model(train_x)
        loss = criterion(output, train_y)
        loss.backward()
        optimizer.step()
        loss_list.append(loss.data)
        print('epoch {}, loss {}'.format(epoch, loss.item()))

epoch 0, loss 0.663551390171051
epoch 0, loss 0.44233381748199463
epoch 0, loss 1.2156074047088623
epoch 0, loss 0.6302769184112549
epoch 0, loss 0.6399853229522705
epoch 0, loss 0.38854750990867615
epoch 0, loss 0.45429882407188416
epoch 0, loss 0.2780325412750244
epoch 0, loss 0.4379619359970093
epoch 0, loss 0.20227402448654175
epoch 0, loss 0.34602537751197815
epoch 0, loss 0.21475987136363983
epoch 0, loss 0.20137356221675873
epoch 0, loss 0.26656174659729004
epoch 0, loss 0.18397876620292664
epoch 0, loss 0.19082613289356232
epoch 0, loss 0.18572036921977997
epoch 0, loss 0.1785762757062912
epoch 0, loss 0.07071982324123383
epoch 0, loss 0.2809423804283142
epoch 0, loss 0.17020581662654877
epoch 0, loss 0.11255928128957748
epoch 0, loss 0.2726343870162964
epoch 0, loss 0.15694278478622437
epoch 0, loss 0.17210836708545685
epoch 0, loss 0.1585868000984192
epoch 0, loss 0.19196033477783203
epoch 0, loss 0.23242595791816711
epoch 0, loss 0.16074182093143463
epoch 0, loss 0.247226968

epoch 0, loss 0.17314249277114868
epoch 0, loss 0.063337542116642
epoch 0, loss 0.1649019867181778
epoch 0, loss 0.17982442677021027
epoch 0, loss 0.131538987159729
epoch 0, loss 0.23368188738822937
epoch 0, loss 0.12424659729003906
epoch 0, loss 0.08165294677019119
epoch 0, loss 0.1557353138923645
epoch 0, loss 0.11126916855573654
epoch 0, loss 0.13604438304901123
epoch 0, loss 0.18191108107566833
epoch 0, loss 0.11382944136857986
epoch 0, loss 0.1033879816532135
epoch 0, loss 0.1076294407248497
epoch 0, loss 0.11866822093725204
epoch 0, loss 0.07271334528923035
epoch 0, loss 0.14167356491088867
epoch 0, loss 0.16030754148960114
epoch 0, loss 0.1525675505399704
epoch 0, loss 0.09566556662321091
epoch 0, loss 0.18718156218528748
epoch 0, loss 0.12172751128673553
epoch 0, loss 0.18818652629852295
epoch 0, loss 0.11020553857088089
epoch 0, loss 0.13180002570152283
epoch 0, loss 0.08057940751314163
epoch 0, loss 0.15970338881015778
epoch 0, loss 0.11839743703603745
epoch 0, loss 0.1982696

epoch 0, loss 0.10950973629951477
epoch 0, loss 0.2479221373796463
epoch 0, loss 0.1418084055185318
epoch 0, loss 0.1496702879667282
epoch 0, loss 0.15776829421520233
epoch 0, loss 0.24077464640140533
epoch 0, loss 0.1602967232465744
epoch 0, loss 0.16756008565425873
epoch 0, loss 0.14163146913051605
epoch 0, loss 0.10469940304756165
epoch 0, loss 0.15404000878334045
epoch 0, loss 0.19119210541248322
epoch 0, loss 0.12039927393198013
epoch 0, loss 0.19316020607948303
epoch 0, loss 0.15025688707828522
epoch 0, loss 0.1251450628042221
epoch 0, loss 0.22873395681381226
epoch 0, loss 0.116173654794693
epoch 0, loss 0.1717294156551361
epoch 0, loss 0.08091125637292862
epoch 0, loss 0.15316803753376007
epoch 0, loss 0.05272282287478447
epoch 0, loss 0.3003208637237549
epoch 0, loss 0.19556017220020294
epoch 0, loss 0.173184335231781
epoch 0, loss 0.14096036553382874
epoch 0, loss 0.1189935952425003
epoch 0, loss 0.17289473116397858
epoch 0, loss 0.1807389110326767
epoch 0, loss 0.16881938278

epoch 0, loss 0.14394015073776245
epoch 0, loss 0.1602257937192917
epoch 0, loss 0.1363229751586914
epoch 0, loss 0.09070859849452972
epoch 0, loss 0.11103761941194534
epoch 0, loss 0.1487325131893158
epoch 0, loss 0.11178983747959137
epoch 0, loss 0.13588130474090576
epoch 0, loss 0.07040698826313019
epoch 0, loss 0.1547330766916275
epoch 0, loss 0.2026505023241043
epoch 0, loss 0.1916213035583496
epoch 0, loss 0.1969972550868988
epoch 0, loss 0.1420840322971344
epoch 0, loss 0.11709102988243103
epoch 0, loss 0.10638844221830368
epoch 0, loss 0.13954156637191772
epoch 0, loss 0.1231331154704094
epoch 0, loss 0.13369077444076538
epoch 0, loss 0.1547732949256897
epoch 0, loss 0.20695781707763672
epoch 0, loss 0.13506823778152466
epoch 0, loss 0.14690056443214417
epoch 0, loss 0.15445077419281006
epoch 0, loss 0.06365891546010971
epoch 0, loss 0.09452563524246216
epoch 0, loss 0.10943689942359924
epoch 0, loss 0.18065756559371948
epoch 0, loss 0.09753448516130447
epoch 0, loss 0.11895764

epoch 1, loss 0.09402342140674591
epoch 1, loss 0.09950309991836548
epoch 1, loss 0.14895081520080566
epoch 1, loss 0.07413868606090546
epoch 1, loss 0.20549973845481873
epoch 1, loss 0.17711950838565826
epoch 1, loss 0.06385492533445358
epoch 1, loss 0.18175092339515686
epoch 1, loss 0.1564847230911255
epoch 1, loss 0.13247960805892944
epoch 1, loss 0.10138442367315292
epoch 1, loss 0.15541142225265503
epoch 1, loss 0.1087360605597496
epoch 1, loss 0.17841950058937073
epoch 1, loss 0.07667425274848938
epoch 1, loss 0.1507723033428192
epoch 1, loss 0.11106033623218536
epoch 1, loss 0.1781046837568283
epoch 1, loss 0.14527234435081482
epoch 1, loss 0.11210459470748901
epoch 1, loss 0.15814276039600372
epoch 1, loss 0.15275424718856812
epoch 1, loss 0.09028774499893188
epoch 1, loss 0.06975415349006653
epoch 1, loss 0.19527503848075867
epoch 1, loss 0.10141530632972717
epoch 1, loss 0.18659010529518127
epoch 1, loss 0.09014295786619186
epoch 1, loss 0.1537065953016281
epoch 1, loss 0.101

...

epoch 99, loss 0.0932227298617363
epoch 99, loss 0.16333389282226562
epoch 99, loss 0.12846845388412476
epoch 99, loss 0.09926359355449677
epoch 99, loss 0.23866532742977142
epoch 99, loss 0.09447570890188217
epoch 99, loss 0.14254428446292877
epoch 99, loss 0.1350775510072708
epoch 99, loss 0.1372998058795929
epoch 99, loss 0.09825549274682999
epoch 99, loss 0.1190413311123848
epoch 99, loss 0.13715188205242157
epoch 99, loss 0.1069895476102829
epoch 99, loss 0.10884001851081848
epoch 99, loss 0.13194076716899872
epoch 99, loss 0.2886762320995331
epoch 99, loss 0.10301712155342102
epoch 99, loss 0.06928595900535583
epoch 99, loss 0.13324755430221558
epoch 99, loss 0.09157460927963257
epoch 99, loss 0.12992893159389496
epoch 99, loss 0.10425577312707901
epoch 99, loss 0.18779082596302032
epoch 99, loss 0.19288916885852814
epoch 99, loss 0.0921231061220169
epoch 99, loss 0.14256960153579712
epoch 99, loss 0.128787562251091
epoch 99, loss 0.18844547867774963
epoch 99, loss 0.075622051954

epoch 99, loss 0.07171829044818878
epoch 99, loss 0.12424633651971817
epoch 99, loss 0.07507088035345078
epoch 99, loss 0.12134678661823273
epoch 99, loss 0.08672267943620682
epoch 99, loss 0.13030508160591125
epoch 99, loss 0.17055338621139526
epoch 99, loss 0.10316517949104309
epoch 99, loss 0.11635933071374893
epoch 99, loss 0.12443895637989044
epoch 99, loss 0.18483075499534607
epoch 99, loss 0.09995973855257034
epoch 99, loss 0.1264031082391739
epoch 99, loss 0.10955487191677094
epoch 99, loss 0.0853646919131279
epoch 99, loss 0.09737109392881393
epoch 99, loss 0.051824845373630524
epoch 99, loss 0.08713147044181824
epoch 99, loss 0.0934041440486908
epoch 99, loss 0.10473139584064484
epoch 99, loss 0.11763688921928406
epoch 99, loss 0.17378392815589905
epoch 99, loss 0.14170506596565247
epoch 99, loss 0.03616713732481003
epoch 99, loss 0.07149697095155716
epoch 99, loss 0.05765220522880554
epoch 99, loss 0.07177776098251343
epoch 99, loss 0.18762467801570892
epoch 99, loss 0.13227

epoch 99, loss 0.09306482970714569
epoch 99, loss 0.11484610289335251
epoch 99, loss 0.09074916690587997
epoch 99, loss 0.10394640266895294
epoch 99, loss 0.09952268749475479
epoch 99, loss 0.14129388332366943
epoch 99, loss 0.1613631695508957
epoch 99, loss 0.10307084023952484
epoch 99, loss 0.13349822163581848
epoch 99, loss 0.07409068942070007
epoch 99, loss 0.11580629646778107
epoch 99, loss 0.10854741185903549
epoch 99, loss 0.2057870328426361
epoch 99, loss 0.09349888563156128
epoch 99, loss 0.07913213968276978
epoch 99, loss 0.18304240703582764
epoch 99, loss 0.08643258363008499
epoch 99, loss 0.0976213812828064
epoch 99, loss 0.0682544931769371
epoch 99, loss 0.2148265391588211
epoch 99, loss 0.12916699051856995
epoch 99, loss 0.16757804155349731
epoch 99, loss 0.12303879112005234
epoch 99, loss 0.058618947863578796
epoch 99, loss 0.11120244860649109
epoch 99, loss 0.05804913491010666
epoch 99, loss 0.08252356201410294
epoch 99, loss 0.08522385358810425
epoch 99, loss 0.0882490

epoch 99, loss 0.1545371264219284
epoch 99, loss 0.12348351627588272
epoch 99, loss 0.145792156457901
epoch 99, loss 0.05258135870099068
epoch 99, loss 0.0666210874915123
epoch 99, loss 0.12114977836608887
epoch 99, loss 0.12128683179616928
epoch 99, loss 0.06647615134716034
epoch 99, loss 0.058711711317300797
epoch 99, loss 0.11363209038972855
epoch 99, loss 0.07759624719619751
epoch 99, loss 0.15058846771717072
epoch 99, loss 0.2165525108575821
epoch 99, loss 0.11230044066905975
epoch 99, loss 0.10030430555343628
epoch 99, loss 0.10651315748691559
epoch 99, loss 0.08101692795753479
epoch 99, loss 0.0502953976392746
epoch 99, loss 0.16012656688690186
epoch 99, loss 0.18855230510234833
epoch 99, loss 0.0985196977853775
epoch 99, loss 0.19115564227104187
epoch 99, loss 0.1395217925310135
epoch 99, loss 0.1912796050310135
epoch 99, loss 0.14808250963687897
epoch 99, loss 0.14718981087207794
epoch 99, loss 0.1268540322780609
epoch 99, loss 0.096387580037117
epoch 99, loss 0.10518708825111

epoch 99, loss 0.1060122400522232
epoch 99, loss 0.17198094725608826
epoch 99, loss 0.13391439616680145
epoch 99, loss 0.07267022877931595
epoch 99, loss 0.1350647360086441
epoch 99, loss 0.12546169757843018
epoch 99, loss 0.08204324543476105
epoch 99, loss 0.14818574488162994
epoch 99, loss 0.070201076567173
epoch 99, loss 0.15256409347057343
epoch 99, loss 0.11292681097984314
epoch 99, loss 0.09021885693073273
epoch 99, loss 0.08918911963701248
epoch 99, loss 0.1056133434176445
epoch 99, loss 0.1226329579949379
epoch 99, loss 0.26963838934898376
epoch 99, loss 0.0982712060213089
epoch 99, loss 0.07968710362911224
epoch 99, loss 0.09791713953018188
epoch 99, loss 0.09254810214042664
epoch 99, loss 0.11406359821557999
epoch 99, loss 0.08103591203689575
epoch 99, loss 0.14291244745254517
epoch 99, loss 0.10692806541919708
epoch 99, loss 0.0847947970032692
epoch 99, loss 0.10863074660301208
epoch 99, loss 0.12647217512130737
epoch 99, loss 0.08765513449907303
epoch 99, loss 0.08330373466

In [18]:
#Calculating correct_rate using the training data
pred_list = list()
test_y_list = list()
with torch.no_grad():
    model.eval()
    correct = 0
    for test_x, test_y in train_loader:
        test_y_list.extend(test_y.to('cpu').detach().numpy().tolist())
        test_x, test_y = Variable(test_x), Variable(test_y)
        test_x = test_x.to(device)
        test_y = test_y.to(device)
        output = model(test_x)
        pred = torch.max(output.data, 1)[1]
        #print(pred)
        pred_list.extend(pred.to('cpu').detach().numpy().tolist())
        correct += pred.eq(test_y.data.view_as(pred)).sum() 
    # correct_rate
    data_num = len(train_loader.dataset)
    print('correct _rate: {}/{} ({:.0f}%)\n'.format(correct, data_num, 100. * correct / data_num))

correct _rate: 115672/122738 (94%)



In [19]:
testdata = df_test.drop(['id', 'label', 'attack_cat'], axis=1)
testlabel = df_test.iloc[:,-1]

#min-max scaling
testdata_norm = (testdata - testdata.min()) / (testdata.max() - testdata.min())
testdata_norm = testdata_norm.fillna(0)

testdata_norm.head(10)

dur     proto   service  state     spkts     dpkts    sbytes  \
87395   1.928715e-02  0.856061  0.416667  0.250  0.000948  0.000729  0.000074   
171525  6.666668e-08  0.901515  0.166667  0.375  0.000105  0.000000  0.000007   
100997  3.536851e-03  0.856061  0.000000  0.000  0.000527  0.000182  0.000076   
106304  1.500000e-07  0.909091  0.000000  0.375  0.000105  0.000000  0.000014   
170606  1.929705e-02  0.856061  0.416667  0.250  0.000948  0.000729  0.000040   
113031  1.333334e-07  0.901515  0.000000  0.375  0.000105  0.000000  0.000011   
70458   1.333334e-07  0.022727  0.000000  0.375  0.000105  0.000000  0.000014   
138025  1.500000e-07  0.901515  0.166667  0.375  0.000105  0.000000  0.000007   
135044  1.166667e-07  0.901515  0.166667  0.375  0.000105  0.000000  0.000007   
161530  5.000001e-08  0.901515  0.166667  0.375  0.000105  0.000000  0.000007   

          dbytes      rate      sttl  ...  ct_dst_ltm  ct_src_dport_ltm  \
87395   0.000024  0.000015  0.996078  ...        0.00              0.00   
171525  0.000000  0.250000  0.996078  ...        0.28              0.26   
100997  0.000006  0.000033  0.243137  ...        0.06              0.06   
106304  0.000000  0.111111  0.996078  ...        0.04              0.04   
170606  0.000024  0.000015  0.996078  ...        0.00              0.02   
113031  0.000000  0.125000  0.996078  ...        0.00              0.00   
70458   0.000000  0.125000  0.996078  ...        0.02              0.02   
138025  0.000000  0.111111  0.996078  ...        0.54              0.52   
135044  0.000000  0.142857  0.996078  ...        0.30              0.30   
161530  0.000000  0.333333  0.996078  ...        0.06              0.06   

        ct_dst_sport_ltm  ct_dst_src_ltm  is_ftp_login  ct_ftp_cmd  \
87395           0.000000        0.062500           0.0         0.0   
171525          0.288889        0.203125           0.0         0.0   
100997          0.000000        0.093750           0.0         0.0   
106304          0.044444        0.046875           0.0         0.0   
170606          0.000000        0.000000           0.0         0.0   
113031          0.000000        0.000000           0.0         0.0   
70458           0.022222        0.031250           0.0         0.0   
138025          0.266667        0.406250           0.0         0.0   
135044          0.333333        0.375000           0.0         0.0   
161530          0.066667        0.296875           0.0         0.0   

        ct_flw_http_mthd  ct_src_ltm  ct_srv_dst  is_sm_ips_ports  
87395           0.000000        0.00    0.000000              0.0  
171525          0.000000        0.26    0.213115              0.0  
100997          0.000000        0.08    0.098361              0.0  
106304          0.000000        0.04    0.049180              0.0  
170606          0.033333        0.36    0.000000              0.0  
113031          0.000000        0.02    0.016393              0.0  
70458           0.000000        0.04    0.032787              0.0  
138025          0.000000        0.52    0.426230              0.0  
135044          0.000000        0.32    0.393443              0.0  
161530          0.000000        0.06    0.311475              0.0  

[10 rows x 42 columns]

In [20]:
test_X = torch.tensor(testdata_norm.values, dtype=torch.float32)
test_Y = torch.tensor(testlabel.values, dtype=torch.long) 

test = TensorDataset(test_X, test_Y)
test_loader = DataLoader(test, batch_size=4096)

In [21]:
with torch.no_grad():
    model.eval()
    correct = 0
    pred_list = list()
    test_y_list = list()
    for test_x, test_y in test_loader:
        test_x, test_y = Variable(test_x), Variable(test_y)
        test_y_list.extend(test_y.to('cpu').detach().numpy().tolist())
        test_x = test_x.to(device)
        test_y = test_y.to(device)
        output = model(test_x)
        pred = torch.max(output.data, 1)[1]
        pred_list.extend(pred.to('cpu').detach().numpy().tolist())
        correct += pred.eq(test_y.data.view_as(pred)).sum() 
    # correct_rate
    data_num = len(test_loader.dataset)
    print('correct _rate: {}/{} ({:.0f}%)\n'.format(correct, data_num, 100. * correct / data_num))

correct _rate: 49509/52603 (94%)



In [22]:
accuracy_score(test_y_list, pred_list)

0.9411820618595897

In [23]:
precision_score(test_y_list, pred_list)

0.9497081152191191

In [24]:
recall_score(test_y_list, pred_list)

0.9649411043969814

In [25]:
f1_score(test_y_list, pred_list)

0.9572640128180335

In [26]:
cm = confusion_matrix(test_y_list, pred_list, labels=[0,1])
print(cm)

[[14857  1835]
 [ 1259 34652]]
